In [1]:
!python3 --version

Python 3.11.13


In [2]:
!pip uninstall -y numpy pandas pycaret

Found existing installation: numpy 2.0.2
Uninstalling numpy-2.0.2:
  Successfully uninstalled numpy-2.0.2
Found existing installation: pandas 2.2.2
Uninstalling pandas-2.2.2:
  Successfully uninstalled pandas-2.2.2


In [3]:
!pip install numpy==1.24.4 pandas==2.0.3

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.3/17.3 MB 145.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.2/12.2 MB 156.7 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
google-colab 1.0.0 requires pandas==2.2.2, but you have pandas 2.0.3 which is incompatible.
blosc2 3.5.1 requires numpy>=1.26, but you have numpy 1.24.4 which is incompatible.
jax 0.5.2 requires numpy>=1.25, but you have numpy 1.24.4 which is incompatible.
jaxlib 0.5.1 requires numpy>=1.25, but you have numpy 1.24.4 which is incompatible.
mizani 0.13.5 requires pandas>=2.2.0, but you have pandas 2.0.3 which is incompatible.
opencv-python-headless 4.12.0.88 requires numpy<2.3.0,>=2; python_version >= "3.9", but you have numpy 1.24.4 which is incompatible.
plotnine 0.14.6 requires pandas>=2.2.0, but you have pandas 2.0.3 which is incompatible.
pymc 5.23.0 req

In [1]:
import numpy, pandas, sklearn
print("numpy:", numpy.__version__)
print("pandas:", pandas.__version__)
print("sklearn:", sklearn.__version__)

numpy: 1.24.4
pandas: 2.0.3
sklearn: 1.6.1


In [2]:
!pip install pycaret==3.3.2

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.4/60.4 kB 4.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.3/46.3 kB 6.3 MB/s eta 0:00:00
INFO: pip is looking at multiple versions of category-encoders to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 486.1/486.1 kB 24.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 106.8/106.8 kB 18.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.8/21.8 MB 110.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 85.4/85.4 kB 15.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.2/302.2 kB 43.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 69.0/69.0 kB 11.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.6/11.6 MB 170.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 82.7/82.7 kB 13.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.

In [1]:
import pandas as pd
import numpy as np
from pycaret.classification import setup

In [2]:
from google.colab import files
uploaded = files.upload()

Saving train.csv to train.csv


In [3]:
!ls /content/

logs.log  sample_data  train.csv


# PART 1 - Univariate Time Series (Store Item Demand)

## Load data and prepare single series

In [9]:
import pandas as pd
import numpy as np
import os

train_path = "/content/train.csv"
df_all = pd.read_csv(train_path, parse_dates=['date'])
df = df_all.sample(n=10000, random_state=42)
print(df.shape)

# Pick one store+item (you can parameterize this in your video)
STORE, ITEM = 1, 1
sdf = df[(df['store']==STORE) & (df['item']==ITEM)].copy()

# Make sure it’s daily, sorted, with a proper DateTimeIndex
sdf = sdf.sort_values('date').set_index('date')
series = sdf['sales'].asfreq('D')  # ensures a daily index with potential NaNs for gaps

# Fill any gaps safely
series = series.interpolate().bfill().ffill()
series.head(), series.tail(), series.index.freq


(10000, 4)


(date
 2013-03-02    13.000000
 2013-03-03    13.021898
 2013-03-04    13.043796
 2013-03-05    13.065693
 2013-03-06    13.087591
 Freq: D, Name: sales, dtype: float64,
 date
 2017-08-12    26.0
 2017-08-13    25.5
 2017-08-14    25.0
 2017-08-15    24.5
 2017-08-16    24.0
 Freq: D, Name: sales, dtype: float64,
 <Day>)

## PyCaret Time Series setup

In [10]:
from pycaret.time_series import *

# Forecast horizon: 30 days
exp = setup(
    data=series,
    fh=30,                  # forecast horizon
    fold=3,                 # time-series CV folds
    fold_strategy='expanding',
    session_id=42,
    seasonal_period=7,      # weekly seasonality often present in retail daily data
    use_gpu=True,
)


Streaming output truncated to the last 5000 lines.
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [W

## Compare models and pick contenders

In [13]:
# Try a broad set and pick top 3
top3 = compare_models(n_select=3, exclude=['auto_arima'])
top3


Processing:   0%|          | 0/115 [00:00<?, ?it/s]

[2025-11-06 04:21:26.310] [CUML] [info] Unused keyword parameter: n_jobs during cuML estimator initialization
[2025-11-06 04:21:26.893] [CUML] [info] Unused keyword parameter: n_jobs during cuML estimator initialization


[BaseCdsDtForecaster(fe_target_rr=[WindowSummarizer(lag_feature={'lag': [7, 6, 5,
                                                                         4, 3, 2,
                                                                         1]},
                                                    n_jobs=1)],
                     regressor=HuberRegressor(), sp=7, window_length=7),
 AutoETS(seasonal='mul', sp=7, trend='add'),
 ExponentialSmoothing(seasonal='mul', sp=7, trend='add')]

In [14]:
best = top3[0]
tuned = tune_model(best)
plot_model(tuned, plot='forecast')


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 3 folds for each of 10 candidates, totalling 30 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 12 concurrent workers.
[Parallel(n_jobs=-1)]: Done  30 out of  30 | elapsed:   10.2s finished


## Finalize and forecast future

In [15]:
final_model = finalize_model(tuned)  # retrains on full history
future_forecast = predict_model(final_model, fh=30)
future_forecast.head(10)


y_pred
2017-08-17  23.5000
2017-08-18  23.0016
2017-08-19  22.4975
2017-08-20  21.9934
2017-08-21  21.4904
2017-08-22  20.9974
2017-08-23  20.5049
2017-08-24  20.0120
2017-08-25  19.5211
2017-08-26  19.0218

In [16]:
plot_model(final_model, plot='forecast')      # fitted + forecast
plot_model(final_model, plot='insample')      # insample fit
plot_model(final_model, plot='residuals')     # residual diagnostics
plot_model(final_model, plot='cv')            # CV folds visual


In sample predictions has not been implemented for this estimator of type 'ForecastingPipeline' in `sktime`. When this is implemented, it will be enabled by default in pycaret.
In sample predictions has not been implemented for this estimator of type 'ForecastingPipeline' in `sktime`. When this is implemented, it will be enabled by default in pycaret.
In sample predictions has not been implemented for this estimator of type 'ForecastingPipeline' in `sktime`. When this is implemented, it will be enabled by default in pycaret.


## Save model

In [17]:
save_model(final_model, "store_item_univariate_best")


Transformation Pipeline and Model Successfully Saved


(ForecastingPipeline(steps=[('forecaster',
                             TransformedTargetForecaster(steps=[('model',
                                                                 ForecastingPipeline(steps=[('forecaster',
                                                                                             TransformedTargetForecaster(steps=[('model',
                                                                                                                                 BaseCdsDtForecaster(fe_target_rr=[WindowSummarizer(lag_feature={'lag': [7,
                                                                                                                                                                                                         6,
                                                                                                                                                                                                         5,
                          

# PART 2 - Univariate with Exogenous Variables (Rossmann Store Sales)

In [18]:
from google.colab import files
uploaded = files.upload()

Saving store_rossman.csv to store_rossman.csv
Saving train_rossman.csv to train_rossman.csv


In [19]:
!ls /content/

logs.log     store_item_univariate_best.pkl  train.csv
sample_data  store_rossman.csv		     train_rossman.csv


## Load + prep (select one store, build exogenous)

In [25]:
import pandas as pd
import numpy as np

train_path = "/content/train_rossman.csv"
store_path = "/content/store_rossman.csv"

df = pd.read_csv(train_path, parse_dates=['Date'])
stores = pd.read_csv(store_path)

# Pick a single Store (e.g., the one with the most observations and open days)
store_counts = df.groupby('Store')['Sales'].count().sort_values(ascending=False)
STORE_ID = int(store_counts.index[0])  # or choose a specific store like 1
# 1) Use all days (do NOT filter Open==1)
sdf = df[df['Store']==STORE_ID].copy()

# 2) Index and sort
sdf = sdf.sort_values('Date').set_index('Date')

# 3) Make sure it's daily and fill accidental gaps
sdf = sdf.asfreq('D')  # gives a daily DateTimeIndex with freq='D'

# 4) Feature engineering AND handling missing
# Target: fill zeros when store was closed, else keep original sales
# If you have an 'Open' column, do:
if 'Open' in sdf.columns:
    sdf['Open'] = sdf['Open'].fillna(0).astype(int)
    # Set Sales=0 on days when store was closed (common Rossmann convention)
    sdf['Sales'] = np.where(sdf['Open']==0, 0, sdf['Sales'])

# Exogenous basics
sdf['Promo'] = sdf['Promo'].fillna(0).astype(int) if 'Promo' in sdf.columns else 0
sdf['SchoolHoliday'] = sdf['SchoolHoliday'].fillna(0).astype(int) if 'SchoolHoliday' in sdf.columns else 0
sdf['StateHoliday'] = sdf['StateHoliday'].fillna('0').astype(str)
sdf['dow'] = sdf.index.dayofweek
sdf['month'] = sdf.index.month

# One-hot the holiday
sdf = pd.get_dummies(sdf, columns=['StateHoliday'], drop_first=True)

# 5) Build modeling frame
target = 'Sales'
exog_cols = [c for c in sdf.columns if c != target]
data_ts = sdf[[target] + exog_cols].copy()

# 6) (Optional) forward/back fill any remaining exog NaNs
for c in exog_cols:
    data_ts[c] = data_ts[c].ffill().bfill()

# 7) Now the index has freq='D', safe for PyCaret
print("freq:", data_ts.index.freq)

data_ts.head()


freq: <Day>


Sales  Store  DayOfWeek  Customers  Open  Promo  SchoolHoliday  \
Date                                                                         
2013-01-01      0      1          2          0     0      0              1   
2013-01-02   5530      1          3        668     1      0              1   
2013-01-03   4327      1          4        578     1      0              1   
2013-01-04   4486      1          5        619     1      0              1   
2013-01-05   4997      1          6        635     1      0              1   

            dow  month  StateHoliday_a  StateHoliday_b  StateHoliday_c  
Date                                                                    
2013-01-01    1      1            True           False           False  
2013-01-02    2      1           False           False           False  
2013-01-03    3      1           False           False           False  
2013-01-04    4      1           False           False           False  
2013-01-05    5      1           False           False           False

## PyCaret TS setup (with exogenous)

In [26]:
from pycaret.time_series import *

exp2 = setup(
    data=data_ts,
    target='Sales',
    fh=14,
    fold=3,
    fold_strategy='expanding',
    session_id=42,
    seasonal_period=7,
    enforce_exogenous=True,
    use_gpu=True
)

Streaming output truncated to the last 5000 lines.
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [W

## Compare, tune, and inspect

In [27]:
best_exog = compare_models()
best_exog


Processing:   0%|          | 0/85 [00:00<?, ?it/s]

[2025-11-06 05:25:16.966] [CUML] [info] Unused keyword parameter: n_jobs during cuML estimator initialization
[2025-11-06 05:25:17.559] [CUML] [info] Unused keyword parameter: n_jobs during cuML estimator initialization


BaseCdsDtForecaster(fe_target_rr=[WindowSummarizer(lag_feature={'lag': [7, 6, 5,
                                                                        4, 3, 2,
                                                                        1]},
                                                   n_jobs=1)],
                    regressor=ExtraTreesRegressor(n_jobs=-1, random_state=42),
                    sp=7, window_length=7)

In [28]:
tuned_exog = tune_model(best_exog)
plot_model(tuned_exog, plot='forecast')
plot_model(tuned_exog, plot='cv')
plot_model(tuned_exog, plot='residuals')


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 3 folds for each of 10 candidates, totalling 30 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 12 concurrent workers.
[Parallel(n_jobs=-1)]: Done  30 out of  30 | elapsed:   13.6s finished


In sample predictions has not been implemented for this estimator of type 'BaseCdsDtForecaster' in `sktime`. When this is implemented, it will be enabled by default in pycaret.
In sample predictions has not been implemented for this estimator of type 'BaseCdsDtForecaster' in `sktime`. When this is implemented, it will be enabled by default in pycaret.


## Finalize and forecast future

In [30]:
final_exog = finalize_model(tuned_exog)


In [34]:
# --- Build X_future automatically, align indexes, and forecast in one go ---

import pandas as pd
import numpy as np
from pycaret.time_series import get_config, predict_model

# ====== CONFIG YOU CAN EDIT ======
fh = 14  # forecast horizon (days)
# =================================

# 0) Sanity checks: do we even have exogenous variables?
exog_present = get_config('exogenous_present')
if not exog_present:
    raise ValueError("This model was not trained with exogenous variables. "
                     "Call predict_model(final_model, fh=...) without X, or retrain with exogenous features.")

# 1) Get training metadata
train_index = get_config('data').index                # training index used by PyCaret
X_train      = get_config('X')                        # training exogenous design matrix
exog_cols    = list(X_train.columns)
exog_dtypes  = X_train.dtypes.to_dict()

# 2) Determine frequency and build the future index
#    We will first create a DatetimeIndex for the future, then convert to PeriodIndex if needed.
#    Try to get a reliable frequency string
freq = getattr(train_index, 'freq', None)
freqstr = None
if freq is not None and hasattr(freq, 'freqstr'):
    freqstr = freq.freqstr
elif hasattr(train_index, 'freqstr') and train_index.freqstr is not None:
    freqstr = train_index.freqstr
else:
    # fall back to inferring frequency
    freqstr = pd.infer_freq(train_index)
    if freqstr is None:
        # default to daily if truly missing (common in retail)
        freqstr = 'D'

# last timestamp to start from
if isinstance(train_index, pd.PeriodIndex):
    last_ts = train_index[-1].to_timestamp()
else:
    last_ts = pd.to_datetime(train_index[-1])

# future datetime index (always build as DatetimeIndex first)
future_dt_index = pd.date_range(
    start=last_ts + pd.tseries.frequencies.to_offset(freqstr),
    periods=fh,
    freq=freqstr
)

# If model trained on PeriodIndex, match that; else keep DatetimeIndex
if isinstance(train_index, pd.PeriodIndex):
    future_index = future_dt_index.to_period(freqstr)
else:
    future_index = future_dt_index

# 3) Create the future exogenous frame with EXACTLY the same columns as training
X_future = pd.DataFrame(index=future_index, columns=exog_cols, dtype=float)

# 4) Populate known/engineered features
#    We'll fill common columns intelligently and default the rest to 0.
#    For calendar features (dow/month/year), compute from a DatetimeIndex view.
dt_index_for_features = future_dt_index  # used to derive calendar features

# Fill common planning/holiday columns if present
if 'Promo' in X_future.columns:
    X_future['Promo'] = 0  # change if you have an actual promo plan

if 'SchoolHoliday' in X_future.columns:
    X_future['SchoolHoliday'] = 0  # change to real calendar if available

# One-hot StateHoliday_* columns -> default to 0 (no holiday) unless you know otherwise
for c in [c for c in X_future.columns if c.startswith('StateHoliday_')]:
    X_future[c] = 0

# Calendar features
if 'dow' in X_future.columns:
    X_future['dow'] = dt_index_for_features.dayofweek
if 'weekday' in X_future.columns:
    X_future['weekday'] = dt_index_for_features.weekday
if 'month' in X_future.columns:
    X_future['month'] = dt_index_for_features.month
if 'year' in X_future.columns:
    X_future['year'] = dt_index_for_features.year
if 'day' in X_future.columns:
    X_future['day'] = dt_index_for_features.day

# Any remaining NaNs -> 0 by default (safe fallback for binary dummies / unknown future)
X_future = X_future.fillna(0)

# 5) Enforce exact dtypes to match training (important for categorical dummies / ints)
for col, dt in exog_dtypes.items():
    if col in X_future.columns:
        try:
            X_future[col] = X_future[col].astype(dt)
        except Exception:
            # If exact cast fails, try a sensible fallback: int for integer-like, else keep as is
            if np.issubdtype(getattr(dt, 'type', dt), np.integer):
                X_future[col] = X_future[col].astype('int64')

# 6) Ensure X_future index type matches training index type (Period vs Datetime)
if isinstance(train_index, pd.PeriodIndex) and not isinstance(X_future.index, pd.PeriodIndex):
    X_future.index = future_dt_index.to_period(freqstr)
elif not isinstance(train_index, pd.PeriodIndex) and not isinstance(X_future.index, pd.DatetimeIndex):
    X_future.index = pd.to_datetime(X_future.index)

# 7) (Optional) Align frequency attribute for DatetimeIndex
if isinstance(train_index, pd.DatetimeIndex) and getattr(train_index, 'freq', None) is not None:
    try:
        X_future = X_future.asfreq(train_index.freq)
    except Exception:
        pass  # if asfreq complains, we can proceed as long as dates match

# 8) Forecast
fcast = predict_model(final_exog, fh=fh, X=X_future)

print("Forecast successful. Preview:")
print(fcast.head())

# If you want to inspect what we constructed:
print("\nX_future summary:")
print(X_future.head())
print("\nIndex types -> train:", type(train_index), "| future:", type(X_future.index))


✅ Forecast successful. Preview:
               y_pred
2015-08-01  3213.8096
2015-08-02 -1392.7793
2015-08-03  2481.8905
2015-08-04  2260.1272
2015-08-05  1881.9275

X_future summary:
            Store  DayOfWeek  Customers  Open  Promo  SchoolHoliday  dow  \
2015-08-01      0          0          0     0      0              0    5   
2015-08-02      0          0          0     0      0              0    6   
2015-08-03      0          0          0     0      0              0    0   
2015-08-04      0          0          0     0      0              0    1   
2015-08-05      0          0          0     0      0              0    2   

            month  StateHoliday_a  StateHoliday_b  StateHoliday_c  
2015-08-01      8           False           False           False  
2015-08-02      8           False           False           False  
2015-08-03      8           False           False           False  
2015-08-04      8           False           False           False  
2015-08-05      8   

## Save the pipeline

In [35]:
save_model(final_exog, "rossmann_exogenous_best")

Transformation Pipeline and Model Successfully Saved


(ForecastingPipeline(steps=[('forecaster',
                             TransformedTargetForecaster(steps=[('model',
                                                                 ForecastingPipeline(steps=[('forecaster',
                                                                                             TransformedTargetForecaster(steps=[('model',
                                                                                                                                 BaseCdsDtForecaster(degree=2,
                                                                                                                                                     fe_target_rr=[WindowSummarizer(lag_feature={'lag': [7,
                                                                                                                                                                                                         6,
                                                                       